In [2]:
import os
import json
import boto3
import sklearn
import socket
from pyspark import SparkContext, SparkConf
from pyspark.sql import SparkSession
from pyspark.sql import functions as F


print('user:', os.environ['JUPYTERHUB_SERVICE_PREFIX'])

def uiWebUrl(self):
    from urllib.parse import urlparse
    web_url = self._jsc.sc().uiWebUrl().get()
    port = urlparse(web_url).port
    return "{}proxy/{}/jobs/".format(os.environ['JUPYTERHUB_SERVICE_PREFIX'], port)

# small fix to enable UI views
SparkContext.uiWebUrl = property(uiWebUrl)

# spark configurtion in local regime 
conf = SparkConf().set('spark.master', 'local[*]').set('spark.driver.memory', '8g')

#some needed objects
sc = SparkContext(conf=conf)
spark = SparkSession(sc)
spark

user: /user/st085838/


ValueError: Cannot run multiple SparkContexts at once; existing SparkContext(app=pyspark-shell, master=local[*]) created by __init__ at <ipython-input-1-930e736913b2>:26 

# Part 1 Dataframe

In [3]:
filepath = "file:///home/jovyan/shared/lectures_folder/84-0.txt"

In [4]:
# read text as a dataframe
from pyspark.sql.functions import monotonically_increasing_id

dataframe= sc.textFile(f"{filepath}")\
     .map(lambda x: (x,))\
     .toDF()\
     .select(F.col("_1").alias("text"))\
     .withColumn("doc_id", monotonically_increasing_id())

In [5]:
dataframe.show(dataframe.count(), False)

+--------------------------------------------------------------------------------------------------------+----------+
|text                                                                                                    |doc_id    |
+--------------------------------------------------------------------------------------------------------+----------+
|The Project Gutenberg eBook of Frankenstein, by Mary Wollstonecraft (Godwin) Shelley                    |0         |
|                                                                                                        |1         |
|This eBook is for the use of anyone anywhere in the United States and                                   |2         |
|most other parts of the world at no cost and with almost no restrictions                                |3         |
|whatsoever. You may copy it, give it away or re-use it under the terms                                  |4         |
|of the Project Gutenberg License included with this eBo

In [6]:
dataframe.count()

7743

In [7]:
#function for filtering out non-letters, creating list of words
from pyspark.sql.functions import udf
from pyspark.sql.types import ArrayType, StringType, IntegerType
import string
import re

def process_string(data):
    non_letters_removed = re.sub(r'[^a-zA-Z]', ' ', data)
    words = non_letters_removed.lower().split(" ") 
    return list(filter(lambda x: len(x) > 0, words))
    
process_string_udf = udf(lambda z: process_string(z), ArrayType(StringType()))

In [8]:
#filter out empty strings,apply function written above
by_words = dataframe\
    .select(process_string_udf(F.col("text")).alias("by_words"))\
    .where(F.size(F.col("by_words")) > 0)\
    .withColumn("doc_id", monotonically_increasing_id())

In [9]:
by_words.show()

+--------------------+------+
|            by_words|doc_id|
+--------------------+------+
|[the, project, gu...|     0|
|[this, ebook, is,...|     1|
|[most, other, par...|     2|
|[whatsoever, you,...|     3|
|[of, the, project...|     4|
|[www, gutenberg, ...|     5|
|[will, have, to, ...|     6|
|[using, this, ebook]|     7|
|[title, frankenst...|     8|
|[or, the, modern,...|     9|
|[author, mary, wo...|    10|
|[release, date, e...|    11|
|[most, recently, ...|    12|
| [language, english]|    13|
|[character, set, ...|    14|
|[produced, by, ju...|    15|
|[further, correct...|    16|
|[start, of, the, ...|    17|
|      [frankenstein]|    18|
|[or, the, modern,...|    19|
+--------------------+------+
only showing top 20 rows



In [10]:
#create a column with separate words in each row
by_words_count = by_words\
     .withColumn('word',(F.explode(F.col("by_words"))))

In [11]:
by_words_count.show()

+--------------------+------+--------------+
|            by_words|doc_id|          word|
+--------------------+------+--------------+
|[the, project, gu...|     0|           the|
|[the, project, gu...|     0|       project|
|[the, project, gu...|     0|     gutenberg|
|[the, project, gu...|     0|         ebook|
|[the, project, gu...|     0|            of|
|[the, project, gu...|     0|  frankenstein|
|[the, project, gu...|     0|            by|
|[the, project, gu...|     0|          mary|
|[the, project, gu...|     0|wollstonecraft|
|[the, project, gu...|     0|        godwin|
|[the, project, gu...|     0|       shelley|
|[this, ebook, is,...|     1|          this|
|[this, ebook, is,...|     1|         ebook|
|[this, ebook, is,...|     1|            is|
|[this, ebook, is,...|     1|           for|
|[this, ebook, is,...|     1|           the|
|[this, ebook, is,...|     1|           use|
|[this, ebook, is,...|     1|            of|
|[this, ebook, is,...|     1|        anyone|
|[this, eb

In [12]:
from pyspark.sql.functions import count

In [48]:
#calculate each term frequency in each document 
by_words_tf= by_words_count\
        .groupBy('doc_id', 'word').count()\
        .orderBy(F.col("doc_id"))\
        .withColumnRenamed("count", 'tf')

In [49]:
by_words_tf.show(by_words_tf.count(), False)

+----------+------------------+---+
|doc_id    |word              |tf |
+----------+------------------+---+
|0         |godwin            |1  |
|0         |project           |1  |
|0         |gutenberg         |1  |
|0         |of                |1  |
|0         |ebook             |1  |
|0         |wollstonecraft    |1  |
|0         |frankenstein      |1  |
|0         |the               |1  |
|0         |mary              |1  |
|0         |shelley           |1  |
|0         |by                |1  |
|1         |use               |1  |
|1         |united            |1  |
|1         |ebook             |1  |
|1         |the               |2  |
|1         |anyone            |1  |
|1         |in                |1  |
|1         |anywhere          |1  |
|1         |and               |1  |
|1         |states            |1  |
|1         |for               |1  |
|1         |this              |1  |
|1         |is                |1  |
|1         |of                |1  |
|2         |with            

In [17]:
#calulate total number of docs
N_docs = by_words.count()
N_docs

6737

In [26]:
from pyspark.sql.functions import countDistinct

In [110]:
#calculate document frequency
by_words_df = by_words_count\
       .groupBy("word")\
       .agg(countDistinct("doc_id").alias("df"))\
       .orderBy(F.col('df').desc())

In [111]:
by_words_df.show(by_words_df.count(), False)

+------------------+----+
|word              |df  |
+------------------+----+
|the               |3284|
|and               |2706|
|of                |2436|
|i                 |2361|
|to                |1901|
|my                |1536|
|a                 |1315|
|in                |1128|
|that              |975 |
|was               |949 |
|me                |799 |
|with              |695 |
|but               |683 |
|had               |649 |
|which             |554 |
|you               |552 |
|he                |552 |
|it                |534 |
|not               |520 |
|for               |507 |
|as                |486 |
|his               |483 |
|by                |480 |
|on                |461 |
|this              |443 |
|from              |387 |
|be                |363 |
|have              |350 |
|when              |325 |
|at                |318 |
|her               |310 |
|is                |305 |
|were              |302 |
|your              |245 |
|or                |244 |
|she        

In [29]:
import numpy as np

In [30]:
#function for calulating IDF
def calcIDF(df):
    IDF = np.log(N_docs/df)
    return IDF
calcIDF_udf = udf(lambda z: calcIDF(z).tolist())

In [31]:
#apply function to the dataframe
by_words_idf = by_words_df\
       .withColumn('idf', calcIDF_udf(F.col("df")))

In [32]:
by_words_idf.show()

+-----+----+------------------+
| word|  df|               idf|
+-----+----+------------------+
|  the|3284| 0.718552530388341|
|  and|2706|0.9121431922299266|
|   of|2436|1.0172573721308722|
|    i|2361| 1.048529463875147|
|   to|1901|1.2652346584722307|
|   my|1536|1.4784330872530422|
|    a|1315| 1.633778056348795|
|   in|1128|1.7871685689026557|
| that| 975|1.9329325299628126|
|  was| 949| 1.959961202350732|
|   me| 799| 2.132009055194385|
| with| 695|2.2714581553958677|
|  but| 683|  2.28887514138987|
|  had| 649|2.3399372842565698|
|which| 554| 2.498205314213376|
|  you| 552|2.5018219546835647|
|   he| 552|2.5018219546835647|
|   it| 534| 2.534974162000465|
|  not| 520|2.5615411893851867|
|  for| 507|2.5868589973694767|
+-----+----+------------------+
only showing top 20 rows



In [33]:
#calculate tf-idf for each word
by_words_tfidf = by_words_tf.select('doc_id', 'word', 'count')\
       .join (by_words_idf, 'word')\
       .orderBy(F.col('doc_id').asc())\
       .withColumn("tf_idf", F.col("count") * F.col("idf"))

In [34]:
by_words_tfidf.show()

+--------------+------+-----+----+------------------+------------------+
|          word|doc_id|count|  df|               idf|            tf_idf|
+--------------+------+-----+----+------------------+------------------+
|           the|     0|    1|3284| 0.718552530388341| 0.718552530388341|
|            of|     0|    1|2436|1.0172573721308722|1.0172573721308722|
|  frankenstein|     0|    1|  31| 5.381382796475513| 5.381382796475513|
|       project|     0|    1|  88| 4.338033186482454| 4.338033186482454|
|          mary|     0|    1|   3|  7.71675771229255|  7.71675771229255|
|            by|     0|    1| 480| 2.641583897058723| 2.641583897058723|
|       shelley|     0|    1|   3|  7.71675771229255|  7.71675771229255|
|         ebook|     0|    1|  13| 6.250420643499123| 6.250420643499123|
|     gutenberg|     0|    1|  96| 4.251021809492824| 4.251021809492824|
|        godwin|     0|    1|   3|  7.71675771229255|  7.71675771229255|
|wollstonecraft|     0|    1|   3|  7.7167577122925

In [45]:
#create tf-idf for each document(row), create final dataframe
by_words_final = by_words_tfidf\
       .groupBy("doc_id").sum("tf_idf")\
       .withColumnRenamed("sum(tf_idf)", 'tf_idf vector')

In [46]:
by_words_final.show()

+------+------------------+
|doc_id|     tf_idf vector|
+------+------------------+
|     0| 55.46528308469805|
|     1| 51.91862506843507|
|     2| 57.02242496716091|
|     3| 67.08770598551247|
|     4|48.723213844898986|
|     5| 52.97018550081891|
|     6|49.338885018292586|
|     7|15.841680726319993|
|     8|13.503605616876229|
|     9|18.489440477629174|
|    10|  37.8906413809028|
|    11| 20.99078888752428|
|    12| 29.33189086045275|
|    13|12.437783151031109|
|    14| 30.13751602443938|
|    15|117.46291648866071|
|    16| 43.13491496340592|
|    17|29.673426050761677|
|    18| 5.381382796475513|
|    19|18.489440477629174|
+------+------------------+
only showing top 20 rows



In [37]:
#check that result is the dataframe
type(by_words_final)

pyspark.sql.dataframe.DataFrame

## Part 2 RDD

In [63]:
#read text as RDD
filepath = "file:///home/jovyan/shared/lectures_folder/84-0.txt"
from pyspark.sql.functions import monotonically_increasing_id

RDD = sc.textFile(f"{filepath}")

RDD.take(5)

['The Project Gutenberg eBook of Frankenstein, by Mary Wollstonecraft (Godwin) Shelley',
 '',
 'This eBook is for the use of anyone anywhere in the United States and',
 'most other parts of the world at no cost and with almost no restrictions',
 'whatsoever. You may copy it, give it away or re-use it under the terms']

In [64]:
#lower letters, create a list of word in each row, delete empty rows
RDD_by_words = RDD\
       .map(lambda text: process_string(text))\
       .filter(lambda x: len(x)>0)

In [65]:
RDD_by_words.collect()

[['the',
  'project',
  'gutenberg',
  'ebook',
  'of',
  'frankenstein',
  'by',
  'mary',
  'wollstonecraft',
  'godwin',
  'shelley'],
 ['this',
  'ebook',
  'is',
  'for',
  'the',
  'use',
  'of',
  'anyone',
  'anywhere',
  'in',
  'the',
  'united',
  'states',
  'and'],
 ['most',
  'other',
  'parts',
  'of',
  'the',
  'world',
  'at',
  'no',
  'cost',
  'and',
  'with',
  'almost',
  'no',
  'restrictions'],
 ['whatsoever',
  'you',
  'may',
  'copy',
  'it',
  'give',
  'it',
  'away',
  'or',
  're',
  'use',
  'it',
  'under',
  'the',
  'terms'],
 ['of',
  'the',
  'project',
  'gutenberg',
  'license',
  'included',
  'with',
  'this',
  'ebook',
  'or',
  'online',
  'at'],
 ['www',
  'gutenberg',
  'org',
  'if',
  'you',
  'are',
  'not',
  'located',
  'in',
  'the',
  'united',
  'states',
  'you'],
 ['will',
  'have',
  'to',
  'check',
  'the',
  'laws',
  'of',
  'the',
  'country',
  'where',
  'you',
  'are',
  'located',
  'before'],
 ['using', 'this', 'ebook

In [66]:
#check if the number of rows equals to the result of part 1 calculation
if RDD_by_words.count() == N_docs:
    print('Numbers of rows are equal for both methods')
else:
    print('Numbers of rows differ by', RDD_by_words.count() - N_docs)

Numbers of rows are equal for both methods


In [68]:
#introduce indices for each document
RDD_by_words = RDD_by_words.zipWithIndex()

In [69]:
RDD_by_words.take(5)

[(['the',
   'project',
   'gutenberg',
   'ebook',
   'of',
   'frankenstein',
   'by',
   'mary',
   'wollstonecraft',
   'godwin',
   'shelley'],
  0),
 (['this',
   'ebook',
   'is',
   'for',
   'the',
   'use',
   'of',
   'anyone',
   'anywhere',
   'in',
   'the',
   'united',
   'states',
   'and'],
  1),
 (['most',
   'other',
   'parts',
   'of',
   'the',
   'world',
   'at',
   'no',
   'cost',
   'and',
   'with',
   'almost',
   'no',
   'restrictions'],
  2),
 (['whatsoever',
   'you',
   'may',
   'copy',
   'it',
   'give',
   'it',
   'away',
   'or',
   're',
   'use',
   'it',
   'under',
   'the',
   'terms'],
  3),
 (['of',
   'the',
   'project',
   'gutenberg',
   'license',
   'included',
   'with',
   'this',
   'ebook',
   'or',
   'online',
   'at'],
  4)]

In [114]:
#apply map function to list all instances of each word in the doc
RDD_tf = RDD_by_words.flatMap(lambda x: [((x[1],i),1) for i in x[0]])

In [115]:
RDD_tf.take(500)

[((0, 'the'), 1),
 ((0, 'project'), 1),
 ((0, 'gutenberg'), 1),
 ((0, 'ebook'), 1),
 ((0, 'of'), 1),
 ((0, 'frankenstein'), 1),
 ((0, 'by'), 1),
 ((0, 'mary'), 1),
 ((0, 'wollstonecraft'), 1),
 ((0, 'godwin'), 1),
 ((0, 'shelley'), 1),
 ((1, 'this'), 1),
 ((1, 'ebook'), 1),
 ((1, 'is'), 1),
 ((1, 'for'), 1),
 ((1, 'the'), 1),
 ((1, 'use'), 1),
 ((1, 'of'), 1),
 ((1, 'anyone'), 1),
 ((1, 'anywhere'), 1),
 ((1, 'in'), 1),
 ((1, 'the'), 1),
 ((1, 'united'), 1),
 ((1, 'states'), 1),
 ((1, 'and'), 1),
 ((2, 'most'), 1),
 ((2, 'other'), 1),
 ((2, 'parts'), 1),
 ((2, 'of'), 1),
 ((2, 'the'), 1),
 ((2, 'world'), 1),
 ((2, 'at'), 1),
 ((2, 'no'), 1),
 ((2, 'cost'), 1),
 ((2, 'and'), 1),
 ((2, 'with'), 1),
 ((2, 'almost'), 1),
 ((2, 'no'), 1),
 ((2, 'restrictions'), 1),
 ((3, 'whatsoever'), 1),
 ((3, 'you'), 1),
 ((3, 'may'), 1),
 ((3, 'copy'), 1),
 ((3, 'it'), 1),
 ((3, 'give'), 1),
 ((3, 'it'), 1),
 ((3, 'away'), 1),
 ((3, 'or'), 1),
 ((3, 're'), 1),
 ((3, 'use'), 1),
 ((3, 'it'), 1),
 ((3, 'u

In [118]:
#apply reduce function to count all instances of each word in each doc
RDD_tf=RDD_tf.reduceByKey(lambda x,y:x+y)

In [119]:
RDD_tf.take(50)

[((0, 'project'), 1),
 ((0, 'gutenberg'), 1),
 ((0, 'ebook'), 1),
 ((0, 'of'), 1),
 ((0, 'mary'), 1),
 ((0, 'shelley'), 1),
 ((1, 'for'), 1),
 ((1, 'the'), 2),
 ((1, 'states'), 1),
 ((1, 'and'), 1),
 ((2, 'other'), 1),
 ((2, 'of'), 1),
 ((2, 'world'), 1),
 ((2, 'at'), 1),
 ((2, 'no'), 2),
 ((2, 'restrictions'), 1),
 ((3, 'you'), 1),
 ((3, 'copy'), 1),
 ((3, 'it'), 3),
 ((3, 'or'), 1),
 ((3, 're'), 1),
 ((3, 'under'), 1),
 ((3, 'the'), 1),
 ((3, 'terms'), 1),
 ((4, 'of'), 1),
 ((4, 'project'), 1),
 ((4, 'gutenberg'), 1),
 ((4, 'this'), 1),
 ((4, 'ebook'), 1),
 ((4, 'online'), 1),
 ((4, 'at'), 1),
 ((5, 'if'), 1),
 ((5, 'you'), 2),
 ((5, 'not'), 1),
 ((5, 'located'), 1),
 ((5, 'the'), 1),
 ((5, 'states'), 1),
 ((6, 'have'), 1),
 ((6, 'check'), 1),
 ((6, 'of'), 1),
 ((6, 'country'), 1),
 ((6, 'where'), 1),
 ((6, 'are'), 1),
 ((6, 'before'), 1),
 ((8, 'title'), 1),
 ((9, 'or'), 1),
 ((9, 'the'), 1),
 ((10, 'mary'), 1),
 ((10, 'shelley'), 1),
 ((11, 'release'), 1)]

In [120]:
#recombine previous rdd to (word - (doc_id - tf))
RDD_2=RDD_tf.map(lambda x: (x[0][1],(x[0][0],x[1])))
RDD_2.collect()

[('project', (0, 1)),
 ('gutenberg', (0, 1)),
 ('ebook', (0, 1)),
 ('of', (0, 1)),
 ('mary', (0, 1)),
 ('shelley', (0, 1)),
 ('for', (1, 1)),
 ('the', (1, 2)),
 ('states', (1, 1)),
 ('and', (1, 1)),
 ('other', (2, 1)),
 ('of', (2, 1)),
 ('world', (2, 1)),
 ('at', (2, 1)),
 ('no', (2, 2)),
 ('restrictions', (2, 1)),
 ('you', (3, 1)),
 ('copy', (3, 1)),
 ('it', (3, 3)),
 ('or', (3, 1)),
 ('re', (3, 1)),
 ('under', (3, 1)),
 ('the', (3, 1)),
 ('terms', (3, 1)),
 ('of', (4, 1)),
 ('project', (4, 1)),
 ('gutenberg', (4, 1)),
 ('this', (4, 1)),
 ('ebook', (4, 1)),
 ('online', (4, 1)),
 ('at', (4, 1)),
 ('if', (5, 1)),
 ('you', (5, 2)),
 ('not', (5, 1)),
 ('located', (5, 1)),
 ('the', (5, 1)),
 ('states', (5, 1)),
 ('have', (6, 1)),
 ('check', (6, 1)),
 ('of', (6, 1)),
 ('country', (6, 1)),
 ('where', (6, 1)),
 ('are', (6, 1)),
 ('before', (6, 1)),
 ('title', (8, 1)),
 ('or', (9, 1)),
 ('the', (9, 1)),
 ('mary', (10, 1)),
 ('shelley', (10, 1)),
 ('release', (11, 1)),
 ('date', (11, 1)),
 ('en

In [122]:
#create an auxiliary rdd (word - 1), where each row is an occurence of a certain word in different documents
RDD_3=RDD_2.map(lambda x: (x[0],1))
RDD_3.collect()


[('project', 1),
 ('gutenberg', 1),
 ('ebook', 1),
 ('of', 1),
 ('mary', 1),
 ('shelley', 1),
 ('for', 1),
 ('the', 1),
 ('states', 1),
 ('and', 1),
 ('other', 1),
 ('of', 1),
 ('world', 1),
 ('at', 1),
 ('no', 1),
 ('restrictions', 1),
 ('you', 1),
 ('copy', 1),
 ('it', 1),
 ('or', 1),
 ('re', 1),
 ('under', 1),
 ('the', 1),
 ('terms', 1),
 ('of', 1),
 ('project', 1),
 ('gutenberg', 1),
 ('this', 1),
 ('ebook', 1),
 ('online', 1),
 ('at', 1),
 ('if', 1),
 ('you', 1),
 ('not', 1),
 ('located', 1),
 ('the', 1),
 ('states', 1),
 ('have', 1),
 ('check', 1),
 ('of', 1),
 ('country', 1),
 ('where', 1),
 ('are', 1),
 ('before', 1),
 ('title', 1),
 ('or', 1),
 ('the', 1),
 ('mary', 1),
 ('shelley', 1),
 ('release', 1),
 ('date', 1),
 ('english', 1),
 ('set', 1),
 ('encoding', 1),
 ('utf', 1),
 ('by', 1),
 ('phillips', 1),
 ('lynn', 1),
 ('hanninen', 1),
 ('and', 1),
 ('david', 1),
 ('meltzer', 1),
 ('further', 1),
 ('leeuw', 1),
 ('the', 1),
 ('frankenstein', 1),
 ('or', 1),
 ('the', 1),
 ('m

In [123]:
#create rdd to calculate document frequency of each word
RDD_df=RDD_3\
       .reduceByKey(lambda x,y:x+y)

In [124]:
RDD_df.takeOrdered(10, key = lambda x: -x[1])

[('the', 3284),
 ('and', 2706),
 ('of', 2436),
 ('i', 2361),
 ('to', 1901),
 ('my', 1536),
 ('a', 1315),
 ('in', 1128),
 ('that', 975),
 ('was', 949)]

In [125]:
#calculate idf for each word
idf=RDD_df.map(lambda x: (x[0], np.log(N_docs/x[1])))
idf.collect()

[('project', 4.338033186482454),
 ('gutenberg', 4.251021809492824),
 ('ebook', 6.250420643499123),
 ('of', 1.0172573721308722),
 ('mary', 7.71675771229255),
 ('shelley', 7.71675771229255),
 ('other', 4.293581423911619),
 ('world', 4.965222399250601),
 ('at', 3.0533186181804832),
 ('no', 3.673706444458),
 ('restrictions', 8.122222820400715),
 ('this', 2.721800230915524),
 ('online', 7.429075639840769),
 ('have', 2.9574368464772003),
 ('check', 7.205932088526559),
 ('country', 4.754926990414241),
 ('where', 4.408650753696406),
 ('are', 3.5896233272474585),
 ('before', 3.811423695015201),
 ('title', 8.122222820400715),
 ('set', 5.770847563237237),
 ('encoding', 8.81537000096066),
 ('utf', 8.81537000096066),
 ('further', 7.71675771229255),
 ('leeuw', 8.81537000096066),
 ('letter', 5.349634098160934),
 ('chapter', 4.944168990052769),
 ('st', 7.023610531732605),
 ('dec', 8.81537000096066),
 ('an', 3.440091593276495),
 ('enterprise', 6.512784907966614),
 ('regarded', 7.023610531732605),
 ('ev

In [126]:
idf.takeOrdered(10, key = lambda x: x[1])

[('the', 0.718552530388341),
 ('and', 0.9121431922299266),
 ('of', 1.0172573721308722),
 ('i', 1.048529463875147),
 ('to', 1.2652346584722307),
 ('my', 1.4784330872530422),
 ('a', 1.633778056348795),
 ('in', 1.7871685689026557),
 ('that', 1.9329325299628126),
 ('was', 1.959961202350732)]

In [129]:
#auxiliary rdd, join 2 rdds, format of the final rdd (word - (doc_id - tf) - idf)
RDD_4 =RDD_2.join(idf)

In [130]:
RDD_4.take(10)

[('gutenberg', ((0, 1), 4.251021809492824)),
 ('gutenberg', ((4, 1), 4.251021809492824)),
 ('gutenberg', ((6440, 1), 4.251021809492824)),
 ('gutenberg', ((6450, 1), 4.251021809492824)),
 ('gutenberg', ((6462, 1), 4.251021809492824)),
 ('gutenberg', ((6464, 1), 4.251021809492824)),
 ('gutenberg', ((6468, 1), 4.251021809492824)),
 ('gutenberg', ((6472, 1), 4.251021809492824)),
 ('gutenberg', ((6486, 1), 4.251021809492824)),
 ('gutenberg', ((6490, 1), 4.251021809492824))]

In [131]:
#auxiliary RDD to recombine rdd into format(doc_id - word - tf - idf - tf*idf)
RDD_5=RDD_4.map(lambda x: (x[1][0][0],(x[0],x[1][0][1],x[1][1],x[1][0][1]*x[1][1]))).sortByKey()
RDD_5.collect()

[(0, ('gutenberg', 1, 4.251021809492824, 4.251021809492824)),
 (0, ('of', 1, 1.0172573721308722, 1.0172573721308722)),
 (0, ('mary', 1, 7.71675771229255, 7.71675771229255)),
 (0, ('shelley', 1, 7.71675771229255, 7.71675771229255)),
 (0, ('the', 1, 0.718552530388341, 0.718552530388341)),
 (0, ('by', 1, 2.641583897058723, 2.641583897058723)),
 (0, ('wollstonecraft', 1, 7.71675771229255, 7.71675771229255)),
 (0, ('project', 1, 4.338033186482454, 4.338033186482454)),
 (0, ('ebook', 1, 6.250420643499123, 6.250420643499123)),
 (0, ('frankenstein', 1, 5.381382796475513, 5.381382796475513)),
 (0, ('godwin', 1, 7.71675771229255, 7.71675771229255)),
 (1, ('of', 1, 1.0172573721308722, 1.0172573721308722)),
 (1, ('in', 1, 1.7871685689026557, 1.7871685689026557)),
 (1, ('the', 2, 0.718552530388341, 1.437105060776682)),
 (1, ('and', 1, 0.9121431922299266, 0.9121431922299266)),
 (1, ('ebook', 1, 6.250420643499123, 6.250420643499123)),
 (1, ('this', 1, 2.721800230915524, 2.721800230915524)),
 (1, ('is

In [132]:
#auxiliary rdd, exclude all info apart from doc_id and tf-idf
RDD_6 = RDD_5.map(lambda x: (x[0], x[1][3]))
RDD_6.collect()

[(0, 4.251021809492824),
 (0, 1.0172573721308722),
 (0, 7.71675771229255),
 (0, 7.71675771229255),
 (0, 0.718552530388341),
 (0, 2.641583897058723),
 (0, 7.71675771229255),
 (0, 4.338033186482454),
 (0, 6.250420643499123),
 (0, 5.381382796475513),
 (0, 7.71675771229255),
 (1, 1.0172573721308722),
 (1, 1.7871685689026557),
 (1, 1.437105060776682),
 (1, 0.9121431922299266),
 (1, 6.250420643499123),
 (1, 2.721800230915524),
 (1, 3.0950582243532483),
 (1, 6.618145423624441),
 (1, 5.67987578503151),
 (1, 5.819637727406669),
 (1, 8.122222820400715),
 (1, 2.5868589973694767),
 (1, 5.870931021794219),
 (2, 1.0172573721308722),
 (2, 4.293581423911619),
 (2, 7.347412888916),
 (2, 0.718552530388341),
 (2, 0.9121431922299266),
 (2, 4.272075218690656),
 (2, 5.126490546846724),
 (2, 7.71675771229255),
 (2, 4.965222399250601),
 (2, 3.0533186181804832),
 (2, 8.122222820400715),
 (2, 2.2714581553958677),
 (2, 7.205932088526559),
 (3, 4.13323877383644),
 (3, 5.637316170612714),
 (3, 4.845078087408538),


In [133]:
#final RDD with doc_id and tf-idf vector for each doc
RDD_final=RDD_6\
      .reduceByKey(lambda x,y:x+y)\
      .sortByKey()
RDD_final.take(10)

[(0, 55.46528308469805),
 (1, 51.91862506843506),
 (2, 57.022424967160916),
 (3, 67.08770598551247),
 (4, 48.72321384489898),
 (5, 52.97018550081891),
 (6, 49.338885018292586),
 (7, 15.841680726319993),
 (8, 13.503605616876229),
 (9, 18.489440477629174)]

In [135]:
#check that the type of output is RDD
type(RDD_final)

pyspark.rdd.PipelinedRDD